# Progetto Finale Corso "Big Data"
La seconda parte del progetto finale consiste nell'addestrare un modello di machine learning in grado di classificare correttamente 
gli articoli nelle loro categorie.
La consegna ci dice di addestrare due modelli, uno che prende come input la colonna "documents" e il secondo sulla colonna "summary" e di confrontare i risultati

In [0]:
! rm /databricks/driver/wikipedia.csv

rm: cannot remove '/databricks/driver/wikipedia.csv': No such file or directory


In [0]:
#  Leggiamo nuovamente il nostro dataset di input
!wget https://proai-datasets.s3.eu-west-3.amazonaws.com/wikipedia.csv
import pandas as pd
dataset = pd.read_csv('/databricks/driver/wikipedia.csv')
spark_df = spark.createDataFrame(dataset)
spark_df = spark_df.drop("Unnamed: 0")
spark_df.write.mode("overwrite").saveAsTable("wikipediaDB")
display(spark_df)

--2024-05-07 03:15:38--  https://proai-datasets.s3.eu-west-3.amazonaws.com/wikipedia.csv
Resolving proai-datasets.s3.eu-west-3.amazonaws.com (proai-datasets.s3.eu-west-3.amazonaws.com)... 3.5.224.103, 3.5.224.12
Connecting to proai-datasets.s3.eu-west-3.amazonaws.com (proai-datasets.s3.eu-west-3.amazonaws.com)|3.5.224.103|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1003477941 (957M) [text/csv]
Saving to: ‘wikipedia.csv’

wikipedia.csv       100%[===================>] 956.99M  19.7MB/s    in 63s     

2024-05-07 03:16:42 (15.2 MB/s) - ‘wikipedia.csv’ saved [1003477941/1003477941]



title summary documents categoria economics economics () is a social science that studies the production, distribution, and consumption of goods and services.economics focuses on the behaviour and interactions of economic agents and how economies work. microeconomics analyzes what's viewed as basic elements in the economy, including individual agents and markets, their interactions, and the outcomes of interactions. individual agents may include, for example, households, firms, buyers, and sellers. macroeconomics analyzes the economy as a system where production, consumption, saving, and investment interact, and factors affecting it: employment of the resources of labour, capital, and land, currency inflation, economic growth, and public policies that have impact on these elements. other broad distinctions within economics include those between positive economics, describing "what is", and normative economics, advocating "what ought to be"; between economic theory and applied economics; between rational and behavioural economics; and between mainstream economics and heterodox economics.economic analysis can be applied throughout society, including business, finance, cybersecurity, health care, engineering and government. it is also applied to such diverse subjects as crime, education, the family, feminism, law, philosophy, politics, religion, social institutions, war, science, and the environment. economics () is a social science that studies the production, distribution, and consumption of goods and services.economics focuses on the behaviour and interactions of economic agents and how economies work. microeconomics analyzes what's viewed as basic elements in the economy, including individual agents and markets, their interactions, and the outcomes of interactions. individual agents may include, for example, households, firms, buyers, and sellers. macroeconomics analyzes the economy as a system where production, consumption, saving, and investment interact, and factors affecting it: employment of the resources of labour, capital, and land, currency inflation, economic growth, and public policies that have impact on these elements. other broad distinctions within economics include those between positive economics, describing "what is", and normative economics, advocating "what ought to be"; between economic theory and applied economics; between rational and behavioural economics; and between mainstream economics and heterodox economics.economic analysis can be applied throughout society, including business, finance, cybersecurity, health care, engineering and government. it is also applied to such diverse subjects as crime, education, the family, feminism, law, philosophy, politics, religion, social institutions, war, science, and the environment. definitions of economics over time the earlier term for the discipline was 'political economy', but since the late 19th century, it has commonly been called 'economics'. the term is ultimately derived from ancient greek οἰκονομία (oikonomia) which is a term for the "way (nomos) to run a household (oikos)", or in other words the know-how of an οἰκονομικός (oikonomikos), or "household or homestead manager". derived terms such as "economy" can therefore often mean "frugal" or "thrifty". by extension then, "political economy" was the way to manage a polis or state. there are a variety of modern definitions of economics; some reflect evolving views of the subject or different views among economists. scottish philosopher adam smith (1776) defined what was then called political economy as "an inquiry into the nature and causes of the wealth of nations", in particular as: a branch of the science of a statesman or legislator [with the twofold objectives of providing] a plentiful revenue or subsistence for the people ... [and] to supply the state or commonwealth with a revenue for the publick services. jean-baptiste say (1803), distinguishing the subject matter from its public-policy uses, def

In [0]:
# Osserviamo di nuovo come sono distribuite le categorie
wiki_1 = spark.sql("""
    select categoria, count(documents) as N_articoli
    from wikipediaDB
    group by categoria
""")
display(wiki_1)

categoria N_articoli finance 9863 energy 10033 humanities 10116 politics 11358 economics 10110 science 10166 sports 10066 culture 10155 trade 10064 pets 10016 technology 10082 transport 10111 research 9930 engineering 10219 medicine 10015

In [0]:

# Verifichiamo se abbiamo valori nulli sia nella colonna categoria che nelle colonne summary e documents
from pyspark.sql.functions import col
null_category_df = spark_df.where(col("categoria").isNull())
if null_category_df.count() > 0:
    print("Ci sono record con valore nullo nella colonna 'categoria':")
    
else:
    print("Non ci sono record con valore nullo nella colonna 'categoria'.")


null_category_df = spark_df.filter(col("documents").isNull())
if null_category_df.count() > 0:
    print("Ci sono record con valore nullo nella colonna 'documents':")
    
else:
    print("Non ci sono record con valore nullo nella colonna 'documents'.")

null_category_df = spark_df.filter(col("summary").isNull())
if null_category_df.count() > 0:
    print("Ci sono record con valore nullo nella colonna 'summary':")
    
else:
    print("Non ci sono record con valore nullo nella colonna 'summary'.")


Non ci sono record con valore nullo nella colonna 'categoria'.
Ci sono record con valore nullo nella colonna 'documents':
Ci sono record con valore nullo nella colonna 'summary':


In [0]:
# Rimuoviamo i valori nulli e verifichiamo nuovamente la conta degli articoli

df_without_nulls = spark_df.na.drop(subset=["documents", "summary"])
articles_per_category = df_without_nulls.groupBy("categoria").count()
# Mostra il numero di articoli per ogni categoria
articles_per_category.show()


+-----------+-----+
|  categoria|count|
+-----------+-----+
|   politics|11358|
|  economics|10110|
|    culture|10155|
|    science|10166|
|     energy|10033|
|     sports|10066|
|    finance| 9863|
| humanities|10116|
|      trade|10064|
|       pets|10016|
| technology|10082|
|  transport|10111|
|   medicine|10015|
|engineering|10219|
|   research| 9930|
+-----------+-----+



Come vediamo ci sono alcune differenze nel numero di articoli per ogni categoria. In particolare, la classe politics conta il numero più alto di articoli, mentre finance il numero minore.
Per evitare problemi dovuti a questo sbilanciamento, estraimo lo stesso numero di articoli da ogni categoria


In [0]:
# Creaimo un nuovo dataframe con lo stesso numero di articoli per ogni categoria
category_counts = df_without_nulls.groupBy("categoria").count()

# Trova il numero minimo di elementi tra le categorie
min_count = category_counts.selectExpr("min(count)").first()[0]


In [0]:
from pyspark.sql.functions import rand
unique_categorie = df_without_nulls.select("categoria").distinct()
equalized_dfs = []
for category in unique_categorie:
    equalized_df = df_without_nulls.filter(col("categoria") == category).orderBy(rand()).limit(min_count)
    equalized_dfs.append(equalized_df)

# Unisci tutti i DataFrame risultanti
equalized_df = equalized_dfs[0]
for df_ in equalized_dfs[1:]:
    equalized_df = equalized_df.union(df_)

## ML model

Per prima cosa, dividiamo il nostro dataset in train e test. Importiamo alcune librerie e vari modelli che testeremo.
L'obiettivo è addestrare diversi modelli e confrontare i risultati tra quelli addestrati con la colonna summary e quella dell'articolo


In [0]:
from pyspark.ml.feature import VectorAssembler, Tokenizer, CountVectorizer,StandardScaler 
from pyspark.ml import Pipeline
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.ml.classification import LogisticRegression, RandomForestClassifier,NaiveBayes
from pyspark.ml.feature import StringIndexer
from pyspark.ml.feature import VectorAssembler
train,test = equalized_df.randomSplit([0.8,0.2],seed=123)

### Logistic Regression
Iniziamo valutando la regressione logistica. 
Creaimo due modelli, il primo che valuta la colonna "documents" e il secondo "summary". Valutiamo l'accuracy del modello

In [0]:


tokenizer1= Tokenizer(inputCol="documents",outputCol="tokens")
counter=CountVectorizer(inputCol="tokens",outputCol="vector",vocabSize=5000)
scaler=StandardScaler(inputCol="vector",outputCol="features")
indexer = StringIndexer(inputCol="categoria", outputCol="categoriaIndex")
lr=LogisticRegression(labelCol="categoriaIndex")
pipeline1=Pipeline(stages=[tokenizer1,counter,scaler,indexer,lr])
model1=pipeline1.fit(train)

In [0]:
test_pred1=model1.transform(test)

evaluator=MulticlassClassificationEvaluator(labelCol="categoriaIndex",metricName="accuracy")
evaluator.evaluate(test_pred1)

Out[50]: 0.8602794411177644

In [0]:
# Cambiamo solo il tokenizer e riduciamo anche il vocabSize. Creaimo una nuova pipeline
tokenizer2= Tokenizer(inputCol="summary",outputCol="tokens")
counter2=CountVectorizer(inputCol="tokens",outputCol="vector",vocabSize=3000)

pipeline2=Pipeline(stages=[tokenizer2,counter2,scaler,indexer,lr])
model2=pipeline2.fit(train)
test_pred2=model2.transform(test)
evaluator.evaluate(test_pred2)

Out[31]: 0.8163672654690619

## Random Forest 


In [0]:

rf = RandomForestClassifier(numTrees=50, maxDepth=20, labelCol="categoriaIndex", seed=42,
leafCol="leafId")
tokenizer1b= Tokenizer(inputCol="documents",outputCol="tokens")
counterb=CountVectorizer(inputCol="tokens",outputCol="vector",vocabSize=5000)
scalerb=StandardScaler(inputCol="vector",outputCol="features")
pipeline3=Pipeline(stages=[tokenizer1b,counterb,scalerb,indexer,rf])
model3=pipeline3.fit(train)

test_pred3=model3.transform(test)
evaluator.evaluate(test_pred3)

Out[53]: 0.8088822355289421

In [0]:
# Proviamo ora con la colonna summary
rf = RandomForestClassifier(numTrees=50, maxDepth=20, labelCol="categoriaIndex", seed=42,
leafCol="leafId")

pipeline4=Pipeline(stages=[tokenizer2,counter2,scaler,indexer,rf])
model4=pipeline4.fit(train)

test_pred4=model4.transform(test)
evaluator.evaluate(test_pred4)

Out[51]: 0.7649700598802395

## Naive Bayes 

Proviamo ora a cambiare modello e utilizzare un modello Naive Bayes

In [0]:
nb = NaiveBayes(smoothing=1.0, modelType="multinomial",labelCol="categoriaIndex")
pipeline5=Pipeline(stages=[tokenizer1,counter,scaler,indexer,nb])
model5=pipeline5.fit(train)

test_pred5=model5.transform(test)
evaluator.evaluate(test_pred5)

Out[20]: 0.8068862275449101

In [0]:
# Colonna "summary"
pipeline6=Pipeline(stages=[tokenizer2,counter2,scaler,indexer,nb])
model6=pipeline6.fit(train)

test_pred6=model6.transform(test)
evaluator.evaluate(test_pred6)

Out[46]: 0.7944111776447106

Il modello migliore per accuracy è il primo che abbiamo allenato.
Proviamo a visualizzare le matrici di confusione delle predizioni

In [0]:
# Modello 1: LogisticRegrression su colonna "documents"

predictions1 = model1.transform(test).select("prediction", "categoriaIndex")

confusion_matrix1 = predictions1.crosstab('prediction', 'categoriaIndex')
confusion_matrix1.show()

+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|prediction_categoriaIndex|0.0|1.0|10.0|11.0|12.0|13.0|14.0|2.0|3.0|4.0|5.0|6.0|7.0|8.0|9.0|
+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|                      0.0|124|  1|   4|   3|   1|   1|   1|  3|  3|  0|  0|  0|  0|  0|  1|
|                      5.0|  0|  1|   0|   0|   0|   0|   1|  0|  2|  1|139|  0|  0|  0|  3|
|                     10.0|  0|  0| 115|   3|   0|   1|   2|  1|  5|  0|  2|  2|  1|  0|  3|
|                     14.0|  1|  0|   5|   1|   1|   2|  89|  0|  0| 37|  0|  2|  0|  1|  0|
|                      1.0|  0|131|   0|   0|   0|   0|   0|  0|  0|  1|  0|  0|  0|  0|  0|
|                      6.0|  1|  0|   2|   1|   1|   0|   0|  1|  1|  1|  2|106|  1|  0|  0|
|                      9.0|  0|  0|   4|   0|   0|   0|   0|  0|  4|  1|  0|  0|  0|  0|127|
|                     13.0|  0|  0|   3|   1|   0| 108|   1|  2|  0|  

In [0]:
# Modello 2: LogisticRegrression su colonna "summary"
predictions2 = model2.transform(test).select("prediction", "categoriaIndex")
confusion_matrix2 = predictions2.crosstab('prediction', 'categoriaIndex')
confusion_matrix2.show()

+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|prediction_categoriaIndex|0.0|1.0|10.0|11.0|12.0|13.0|14.0|2.0|3.0|4.0|5.0|6.0|7.0|8.0|9.0|
+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|                      0.0|119|  1|   6|   1|   0|   0|   3|  4|  6|  2|  1|  0|  0|  1|  1|
|                      5.0|  0|  0|   3|   0|   1|   0|   1|  1|  1|  1|131|  3|  2|  1|  1|
|                     10.0|  4|  0| 114|   2|   5|   1|   6|  1|  4|  3|  5|  2|  2|  3|  9|
|                     14.0|  2|  0|   3|   0|   0|   2|  71|  0|  0| 23|  1|  1|  1|  4|  1|
|                      1.0|  0|130|   0|   0|   0|   0|   0|  0|  0|  0|  0|  0|  0|  0|  0|
|                      6.0|  0|  1|   1|   0|   1|   1|   1|  0|  3|  0|  0|101|  0|  0|  0|
|                      9.0|  0|  0|   1|   0|   1|   0|   1|  1|  5|  1|  0|  0|  1|  0|121|
|                     13.0|  0|  0|   3|   1|   2| 106|   2|  1|  0|  

In [0]:
# Modello 3: RandomForest su colonna "documents"
predictions3 = model3.transform(test).select("prediction", "categoriaIndex")
confusion_matrix3 = predictions3.crosstab('prediction', 'categoriaIndex')
confusion_matrix3.show()

+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|prediction_categoriaIndex|0.0|1.0|10.0|11.0|12.0|13.0|14.0|2.0|3.0|4.0|5.0|6.0|7.0|8.0|9.0|
+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|                      0.0|121|  0|   2|   2|   0|   0|   0| 14|  7|  1|  0|  0|  1|  1|  0|
|                      5.0|  1|  0|   1|   0|   0|   0|   0|  0|  4|  0|130|  0|  1|  0|  2|
|                     10.0|  2|  1|  89|   3|   9|   2|   6|  0|  2|  2|  3|  0|  2|  1|  1|
|                     14.0|  0|  1|   0|   0|   0|   1|  51|  0|  2|  8|  0|  1|  0|  0|  0|
|                      1.0|  0|130|   0|   0|   0|   1|   0|  0|  0|  0|  0|  0|  0|  0|  0|
|                      6.0|  0|  0|   1|   0|   2|   1|   0|  1|  1|  0|  2|107|  1|  0|  0|
|                      9.0|  1|  2|   7|   0|   0|   0|   0|  2|  4|  0|  0|  1|  0|  0|128|
|                     13.0|  0|  0|   4|   0|   2|  94|   2|  0|  0|  

In [0]:
# Modello 4: RandomForest su colonna "summary"
predictions4 = model4.transform(test).select("prediction", "categoriaIndex")
confusion_matrix4 = predictions4.crosstab('prediction', 'categoriaIndex')
confusion_matrix4.show()

+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|prediction_categoriaIndex|0.0|1.0|10.0|11.0|12.0|13.0|14.0|2.0|3.0|4.0|5.0|6.0|7.0|8.0|9.0|
+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|                      0.0|114|  0|   3|   0|   0|   0|   0|  8| 11|  0|  0|  0|  0|  0|  0|
|                      5.0|  0|  0|   0|   0|   0|   1|   0|  1|  3|  1|125|  0|  0|  0|  1|
|                     10.0| 10|  1|  92|   6|   8|   2|  13|  1|  3|  3|  6|  2|  1|  1|  1|
|                     14.0|  1|  1|   2|   0|   0|   0|  48|  0|  0|  6|  0|  2|  0|  0|  0|
|                      1.0|  0|129|   0|   0|   0|   0|   0|  0|  1|  0|  0|  0|  0|  1|  0|
|                      6.0|  1|  0|   2|   0|   2|   0|   1|  0|  1|  0|  2|102|  1|  0|  0|
|                      9.0|  0|  0|   6|   0|   0|   1|   1|  1|  6|  0|  0|  1|  1|  0|130|
|                     13.0|  0|  0|   1|   0|   1|  95|   0|  0|  0|  

In [0]:
# Modello 5: NaiveBayes su colonna "documents"
predictions5 = model5.transform(test).select("prediction", "categoriaIndex")
confusion_matrix5 = predictions5.crosstab('prediction', 'categoriaIndex')
confusion_matrix5.show()

+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|prediction_categoriaIndex|0.0|1.0|10.0|11.0|12.0|13.0|14.0|2.0|3.0|4.0|5.0|6.0|7.0|8.0|9.0|
+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|                      0.0|120|  0|   2|   0|   0|   0|   0|  6|  0|  2|  0|  0|  0|  0|  0|
|                      5.0|  0|  1|   0|   0|   0|   3|   0|  0|  3|  0|135|  2|  0|  0|  4|
|                     10.0|  0|  0|  64|   2|   2|   0|   1|  0|  0|  0|  1|  1|  0|  0|  0|
|                     14.0|  2|  0|   3|   1|   1|   1|  54|  0|  0|  9|  1|  3|  0|  0|  0|
|                      1.0|  0|129|   0|   0|   0|   0|   0|  0|  0|  0|  0|  0|  0|  0|  0|
|                      6.0|  0|  0|   1|   0|   1|   0|   1|  0|  1|  0|  2|105|  2|  0|  0|
|                      9.0|  0|  0|  30|   0|   0|   0|   0|  2|  2|  1|  0|  0|  0|  0|130|
|                     13.0|  0|  0|   3|   0|   0| 105|   4|  0|  0|  

In [0]:
# Modello 6: NaiveBayes su colonna "summary"
predictions6 = model6.transform(test).select("prediction", "categoriaIndex")
confusion_matrix6 = predictions6.crosstab('prediction', 'categoriaIndex')
confusion_matrix6.show()

+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|prediction_categoriaIndex|0.0|1.0|10.0|11.0|12.0|13.0|14.0|2.0|3.0|4.0|5.0|6.0|7.0|8.0|9.0|
+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|                      0.0|121|  0|   1|   0|   0|   0|   0|  2|  0|  2|  0|  0|  0|  0|  0|
|                      5.0|  0|  1|   0|   0|   1|   1|   0|  0|  1|  0|131|  1|  0|  0|  0|
|                     10.0|  2|  1| 113|   3|   6|   0|   3|  2|  1|  0|  3|  1|  4|  1|  1|
|                     14.0|  2|  0|   1|   2|   0|   2|  60|  0|  0|  7|  1|  2|  0|  0|  0|
|                      1.0|  0|129|   0|   0|   0|   0|   0|  0|  0|  0|  0|  0|  0|  0|  0|
|                      6.0|  0|  0|   0|   0|   1|   0|   2|  0|  2|  0|  0|103|  1|  0|  0|
|                      9.0|  0|  0|   7|   0|   0|   0|   0|  0|  2|  0|  0|  0|  0|  0|131|
|                     13.0|  0|  0|   0|   0|   3|  97|   1|  0|  1|  

## Parte finale 

Il modello che a livello di accuracy ha performato meglio è il primo: logisticRegression sulla colonna "documents".
Proviamo a vedere se utilizzando lo stesso VocabSize anche per la colonna "summary", le performance del secondo modello migliorano.



In [0]:

counter2_bis=CountVectorizer(inputCol="tokens",outputCol="vector",vocabSize=5000)
pipeline2_bis=Pipeline(stages=[tokenizer2,counter2_bis,scaler,indexer,lr])
model2_bis=pipeline2_bis.fit(train)
test_pred2_bis=model2_bis.transform(test)
evaluator.evaluate(test_pred2_bis)

Out[54]: 0.8218562874251497

Le prestazioni migliorano leggermente. Vediamo anche la confusion matrix

In [0]:
predictions2_bis = model2_bis.transform(test).select("prediction", "categoriaIndex")
confusion_matrix2_bis = predictions2_bis.crosstab('prediction', 'categoriaIndex')
confusion_matrix2_bis.show()

+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|prediction_categoriaIndex|0.0|1.0|10.0|11.0|12.0|13.0|14.0|2.0|3.0|4.0|5.0|6.0|7.0|8.0|9.0|
+-------------------------+---+---+----+----+----+----+----+---+---+---+---+---+---+---+---+
|                      0.0|114|  0|   1|   2|   0|   0|   0|  2|  6|  2|  0|  0|  0|  0|  0|
|                      5.0|  1|  0|   1|   0|   1|   0|   0|  2|  3|  0|136|  4|  2|  3|  1|
|                     10.0|  3|  0| 118|   3|   3|   0|   4|  1|  2|  1|  4|  1|  3|  3|  6|
|                     14.0|  4|  0|   3|   1|   0|   3|  73|  1|  1| 21|  2|  1|  1|  6|  1|
|                      1.0|  0|130|   0|   0|   0|   0|   0|  0|  0|  0|  0|  0|  0|  1|  0|
|                      6.0|  0|  0|   0|   0|   1|   2|   1|  0|  2|  2|  2| 99|  0|  0|  0|
|                      9.0|  0|  0|   4|   0|   1|   0|   0|  1|  5|  0|  0|  0|  1|  0|124|
|                     13.0|  0|  1|   2|   0|   1| 109|   2|  2|  3|  